In [5]:
using Plots
plotly()
using STFR: getrf # to design an initial pulse we can simulate
using ForwardDiff
using MAT # to load a previously designed b1-selective pulse
using ProgressMeter
using MatrixDepot
γ = 2 * π * 4258
γbar = 4258

4258

In [6]:
vars = matread("/Users/guille/Dropbox/code/GrisRFEncoding/longshotRF/halfPulse.mat")

Dict{String, Any} with 10 entries:
  "d1e"   => 0.01
  "pbc"   => 1.0
  "ptype" => "st"
  "tb"    => 4.0
  "d2e"   => 0.01
  "dt"    => 2.0e-6
  "flip"  => 1.5708
  "om1"   => [-1.0; -1.0; … ; 1.0; 1.0]
  "dom"   => [-55.491; -166.292; … ; -166.224; -55.4835]
  "pbw"   => 1.0

In [7]:
om1 = vars["om1"]
dom = vars["dom"]
dt = vars["dt"]
tb = vars["tb"]
d1e = vars["d1e"]
d2e = vars["d2e"]
flip = vars["flip"]

1.5707963267948966

In [8]:
# Define a blochsim function for a half pulse
function BlochSimHalfB1Sel(α)
       
    # α: vector of RF rotations (dom), plus a gradient rotation (om1) at the end

    N = length(α) - 1 # number of points in half of pulse

    # initialize magnetization
    Mx = 1.0
    My = 0.0
    Mz = 0.0
    
    # pre-calculate gradient rotation params
    cg = cos(α[end])
    sg = sin(α[end])
    
    # apply first half of pulse
    for ii = 1 : length(α) - 1
        
        # calculate RF rotation params
        crf = cos(α[ii])
        srf = sin(α[ii])
        
        # apply RF rotation
        Myi = My
        Mzi = Mz
        My = crf * Myi + srf * Mzi
        Mz = -srf * Myi + crf * Mzi
        
        # apply gradient rotation
        Mxi = Mx
        Myi = My
        Mx = cg * Mxi + sg * Myi
        My = -sg * Mxi + cg * Myi
            
    end
    
    # apply second half of pulse - note the reversed gradient rotations
    for ii = length(α) - 1 : -1 : 1
        
        # calculate RF rotation params
        crf = cos(α[ii])
        srf = sin(α[ii])
        
        # apply RF rotation
        Myi = My
        Mzi = Mz
        My = crf * Myi + srf * Mzi
        Mz = -srf * Myi + crf * Mzi
        
        # apply gradient rotation
        Mxi = Mx
        Myi = My
        Mx = cg * Mxi - sg * Myi
        My = sg * Mxi + cg * Myi
            
    end
    
    return Mx, My, Mz
    
end

BlochSimHalfB1Sel (generic function with 1 method)

In [9]:
# set up a simulation grid
# we will interpret dom as the RF waveform, which will be colinear with M0
# om1 will be the gradient waveform, which will be scaled by B1+ 
b1 = -5 : 0.01 : 5
nb1 = length(b1)

1001

In [10]:
# Simulate to check that magnitude is same as BlochSim.jl, and get target pattern to recover the pulse
Mx = zeros(nb1, 1) # Mz
My = zeros(nb1, 1) # Mx
Mz = zeros(nb1, 1) # My
nT = length(dom)
for ii = 1 : nb1
    rfg = [dom[1 : Int64(nT / 2)] * 2 * π * dt; b1[ii] * γ * dt];
    M = BlochSimHalfB1Sel(rfg)
    Mx[ii] = M[1]
    My[ii] = M[2]
    Mz[ii] = M[3]
end
plot(b1, abs.(Complex.(My, Mz)), label="|Mxy|", xlabel="Gauss")
plot!(b1, My, label="Mx")
plot!(b1, Mz, label="My")

<!DOCTYPE html>
 
 
 Plots.jl

In [11]:
# define a BlochSim we can use to calculate error, which encapsulates the b1-selective half-pulse blochsim
function myBlochSimErr(α)
       
    # α: vector of RF rotations, plus a gradient rotation at the end, plus a target vector, plus an error weight
        
    Mxd = α[end-3]
    Myd = α[end-2]
    Mzd = α[end-1]     
    w = α[end]
    
    Mx, My, Mz = BlochSimHalfB1Sel(α[1 : end - 4])
    
    err = w * ((Mx - Mxd)^2 + (My - Myd)^2 + (Mz - Mzd)^2)
    
    return err
    
end

myBlochSimErr (generic function with 1 method)

In [12]:
# let's try to recover the pattern above, starting with a zero pulse
step = 0.00001
domoc = zeros(Int64(nT / 2), 1)
niters = 20
g = x -> ForwardDiff.gradient(myBlochSimErr, x)
#h = x -> ForwardDiff.hessian(myBlochSimErr, x)
@showprogress 1 "Computing..." for nn = 1 : niters
    J = zeros(Int64(nT / 2), 1)
    for ii = 1 : nb1
        rfg = [domoc[1 : Int64(nT / 2)]; 
            b1[ii] * γ * dt; Mx[ii]; My[ii]; Mz[ii]; 1.0]
        J += g(rfg)[1 : end - 5] 
        #H += h(rfg)[1 : end - 4, 1 : end - 4]
    end
    domoc -= step * J
end
plot(domoc ./ (2 * π * dt), label="designed")
plot!(dom[1 : Int64(nT / 2)], label="target")
plot!(dom[1 : Int64(nT / 2)] - domoc ./ (2 * π * dt), label="error")

Computing...100%|███████████████████████████████████████| Time: 0:00:13


<!DOCTYPE html>
 
 
 Plots.jl

In [ ]:
# let's try to refine it for zero phase, so that Mz = the magnitude of the above design, and others are zero
step = 0.00001
domoc = dom[1 : Int64(nT / 2)] * 2 * π * dt
niters = 100
g = x -> ForwardDiff.gradient(myBlochSimErr, x)
#h = x -> ForwardDiff.hessian(myBlochSimErr, x)
@showprogress 1 "Computing..." for nn = 1 : niters
    J = zeros(Int64(nT / 2), 1)
    for ii = 1 : Int64((nb1 - 1) / 2)
        rfg = [domoc[1 : Int64(nT / 2)]; 
            b1[ii] * γ * dt; 0.0; 0.0; abs.(Complex.(My[ii], Mz[ii])); 1.0]
        J += g(rfg)[1 : end - 5] 
        #H += h(rfg)[1 : end - 4, 1 : end - 4]
    end
    domoc -= step * J
end
plot(domoc ./ (2 * π * dt), label="refined")
plot!(dom[1 : Int64(nT / 2)], label="original")


In [ ]:
Mxr = zeros(nb1, 1) # Mz
Myr = zeros(nb1, 1) # Mx
Mzr = zeros(nb1, 1) # My
nT = length(dom)
for ii = 1 : nb1
    rfg = [domoc[1 : Int64(nT / 2)]; b1[ii] * γ * dt];
    M = BlochSimHalfB1Sel(rfg)
    Mxr[ii] = M[1]
    Myr[ii] = M[2]
    Mzr[ii] = M[3]
end
plot(b1, abs.(Complex.(Myr, Mzr)), label="|Mxy|", xlabel="Gauss")
plot!(b1, Myr, label="Mx")
plot!(b1, Mzr, label="My")
plot!(b1, abs.(Complex.(My, Mz)), label="|Mxy| desired")

In [ ]:
# now let's properly define a target pattern with positive and negative components and do another oc design
# if this doesn't work, then let's try a full-waveform design

In [13]:
# now let's set up our own target patterns
function dinf(d1, d2)

    a1 = 5.309e-3
    a2 = 7.114e-2
    a3 = -4.761e-1
    a4 = -2.66e-3
    a5 = -5.941e-1
    a6 = -4.278e-1

    l10d1 = log10(d1)
    l10d2 = log10(d2)

    d = (a1 * l10d1^2 + a2 * l10d1 + a3) * l10d2 + (a4 * l10d1^2 + a5 * l10d1 + a6)
    
    return d
    
end

dinf (generic function with 1 method)

In [54]:
ftw = dinf(sqrt(d1e / 2.0), d2e / sqrt(2.0)) / tb # 90-degree transition width relationship
# set up target pattern
N = 128
nCent = 16
f = [0, (1 - ftw) * (tb / 2), (1 + ftw) * (tb / 2), (N / 2)] / (N / 2)
os = 8
x = (-N / 2 : 1 / os : N / 2 - 1 / os)
Mxd = ones(N * os, 1)
Myd = zeros(N * os, 1)
Mzd = zeros(N * os, 1)
θ = π / 4 # flip angle
Mzd[abs.(collect(x .- nCent) ./ (N / 2)) .< f[2]] .= sin(θ)
Mzd[abs.(collect(x .+ nCent) ./ (N / 2)) .< f[2]] .= -sin(θ)
Mxd[abs.(collect(x .- nCent) ./ (N / 2)) .< f[2]] .= cos(θ)
Mxd[abs.(collect(x .+ nCent) ./ (N / 2)) .< f[2]] .= cos(θ)

w = ones(N * os, 1)
w[abs.(collect(x .- nCent) ./ (N / 2)) .< f[3]] .= 0
w[abs.(collect(x .- nCent) ./ (N / 2)) .< f[2]] .= d1e / d2e
w[abs.(collect(x .+ nCent) ./ (N / 2)) .< f[3]] .= 0
w[abs.(collect(x .+ nCent) ./ (N / 2)) .< f[2]] .= d1e / d2e

plot(x, Mxd, label="Mx desired")
plot!(x, Myd, label="My desired")
plot!(x, Mzd, label="Mz desired")
plot!(x, w, label="weights")

<!DOCTYPE html>
 
 
 Plots.jl

In [55]:
# Define a blochsim function for a half pulse - full-FM waveform version
function BlochSimHalfB1Sel(α)
       
    # α: vector of RF rotations (dom), plus a gradient rotation (om1) at the end

    N = length(α) - 1 # number of points in pulse

    # initialize magnetization
    Mx = 1.0
    My = 0.0
    Mz = 0.0
    
    # pre-calculate gradient rotation params
    cg = cos(α[end])
    sg = sin(α[end])
    
    # apply first half of pulse
    for ii = 1 : Int64(N / 2)
        
        # calculate RF rotation params
        crf = cos(α[ii])
        srf = sin(α[ii])
        
        # apply RF rotation
        Myi = My
        Mzi = Mz
        My = crf * Myi + srf * Mzi
        Mz = -srf * Myi + crf * Mzi
        
        # apply gradient rotation
        Mxi = Mx
        Myi = My
        Mx = cg * Mxi + sg * Myi
        My = -sg * Mxi + cg * Myi
            
    end
    
    # apply second half of pulse - note the reversed gradient rotations
    for ii = Int64(N / 2) + 1 : N
        
        # apply gradient rotation
        Mxi = Mx
        Myi = My
        Mx = cg * Mxi - sg * Myi
        My = sg * Mxi + cg * Myi
        
        # calculate RF rotation params
        crf = cos(α[ii])
        srf = sin(α[ii])
        
        # apply RF rotation
        Myi = My
        Mzi = Mz
        My = crf * Myi + srf * Mzi
        Mz = -srf * Myi + crf * Mzi
            
    end
    
    return Mx, My, Mz
    
end

BlochSimHalfB1Sel (generic function with 1 method)

In [56]:
# let's try to design it for zero phase, so that Mz = the magnitude of the above design, and others are zero
step = 0.0001
domoc = zeros(N, 1)
niters = 500
lamda = 10^-2
J = zeros(N, 1)
g = x -> ForwardDiff.gradient(myBlochSimErr, x)
@showprogress 1 "Computing..." for nn = 1 : niters
    J *= 0
    for ii = 1 : N * os
        rfg = [domoc; 2 * π * x[ii] / N; Mxd[ii]; Myd[ii]; Mzd[ii]; w[ii]]
        J += g(rfg)[1 : end - 5] .+ lamda * domoc
    end
    domoc -= step * J
end
plot(domoc ./ (2 * π * dt))
plot!(J)

Computing...100%|███████████████████████████████████████| Time: 0:01:06


<!DOCTYPE html>
 
 
 Plots.jl

In [57]:
# simulate it
Mxr = zeros(N * os, 1) # Mz
Myr = zeros(N * os, 1) # Mx
Mzr = zeros(N * os, 1) # My
for ii = 1 : N * os
    rfg = [domoc; 2 * π * x[ii] / N];
    M = BlochSimHalfB1Sel(rfg)
    Mxr[ii] = M[1]
    Myr[ii] = M[2]
    Mzr[ii] = M[3]
end
plot(x, abs.(Complex.(Myr, Mzr)), label="|Mxy|")
plot!(x, Myr, label="Mx")
plot!(x, Mzr, label="My")
plot!(x, Mzd, label="My, desired")
#plot!(x, abs.(Complex.(My, Mz)), label="|Mxy| desired")

<!DOCTYPE html>
 
 
 Plots.jl

In [ ]:
# Now let's see if we lose anything by forcing it to be symmetric
step = 0.0001
domoc = zeros(Int64(N / 2), 1)
niters = 500
lamda = 0 #10^(-1)
J = zeros(N, 1)
g = x -> ForwardDiff.gradient(myBlochSimErr, x)
@showprogress 1 "Computing..." for nn = 1 : niters
    J *= 0
    for ii = 1 : N * os
        rfg = [domoc; domoc[end : -1 : 1]; 2 * π * x[ii] / N; Mxd[ii]; Myd[ii]; Mzd[ii]; w[ii]]
        J += g(rfg)[1 : end - 5]
    end
    domoc -= step * (J[1 : Int64(N / 2)] .+ J[end : -1 : Int64(N / 2 + 1)])
end
plot(domoc ./ (2 * π * dt))
plot!(J)

In [ ]:
# simulate the half-half pulse design - much worse!
Mxr = zeros(N * os, 1) # Mz
Myr = zeros(N * os, 1) # Mx
Mzr = zeros(N * os, 1) # My
for ii = 1 : N * os
    rfg = [domoc; domoc[end : -1 : 1]; 2 * π * x[ii] / N];
    M = BlochSimHalfB1Sel(rfg)
    Mxr[ii] = M[1]
    Myr[ii] = M[2]
    Mzr[ii] = M[3]
end
plot(x, abs.(Complex.(Myr, Mzr)), label="|Mxy|", xlabel="Gauss")
plot!(x, Myr, label="Mx")
plot!(x, Mzr, label="My")
plot!(x, Mzd, label="My, desired")
#plot!(x, abs.(Complex.(My, Mz)), label="|Mxy| desired")

In [ ]:
# next I want to try zero-padding the pulse out a bit 
# - can we get a flatter phase if we don't demand as tight a slice?
Npad = 192
step = 0.0001
domoc = zeros(Npad, 1)
niters = 500
lamda = 10^-2
J = zeros(Npad, 1)
g = x -> ForwardDiff.gradient(myBlochSimErr, x)
@showprogress 1 "Computing..." for nn = 1 : niters
    J *= 0
    for ii = 1 : N * os
        rfg = [domoc; 2 * π * x[ii] / N; Mxd[ii]; Myd[ii]; Mzd[ii]; w[ii]]
        J += g(rfg)[1 : end - 5] .+ lamda * domoc
    end
    domoc -= step * J
end
plot(domoc ./ (2 * π * dt))
plot!(J)

In [ ]:
# simulate it - it definitely helps in the passband, not so much in transition band
Mxr = zeros(N * os, 1) # Mz
Myr = zeros(N * os, 1) # Mx
Mzr = zeros(N * os, 1) # My
for ii = 1 : N * os
    rfg = [domoc; 2 * π * x[ii] / N];
    M = BlochSimHalfB1Sel(rfg)
    Mxr[ii] = M[1]
    Myr[ii] = M[2]
    Mzr[ii] = M[3]
end
plot(x, abs.(Complex.(Myr, Mzr)), label="|Mxy|", xlabel="Gauss")
plot!(x, Myr, label="Mx")
plot!(x, Mzr, label="My")
plot!(x, Mzd, label="My, desired")
#plot!(x, abs.(Complex.(My, Mz)), label="|Mxy| desired")

In [58]:
# How to convert selection axis to b1+? 
# TB = T (ms) * B (kHz). B = pbw (Gauss) * γbar (Hz / Gauss). So TB and B set pulse duration.
# Then we need to know where the slice position is, in integer units. 
# pbc * γbar = Hz, then T * that gives cycles? 

# for example, let's say our design above is for pbw = 1 Gauss. 
T = tb / (pbw * γbar) # seconds
@show pbc = nCent / (γbar * T)
@show T
@show nb1
@show length(b1)

pbw = tb / (T * γbar) = 1.0
pbc = nCent / (γbar * T) = 2.0
T = 0.0018788163457022077
nb1 = 1001
length(b1) = 1001


1001

In [59]:
# simulate it - checks out!
Mxr = zeros(nb1, 1) # Mz
Myr = zeros(nb1, 1) # Mx
Mzr = zeros(nb1, 1) # My
for ii = 1 : nb1
    rfg = [domoc; b1[ii] * γ * T / N]
    M = BlochSimHalfB1Sel(rfg)
    Mxr[ii] = M[1]
    Myr[ii] = M[2]
    Mzr[ii] = M[3]
end
plot(b1, abs.(Complex.(Myr, Mzr)), label="|Mxy|")
plot!(b1, Myr, label="Mx")
plot!(b1, Mzr, label="My")
#plot!(x, abs.(Complex.(My, Mz)), label="|Mxy| desired")

<!DOCTYPE html>
 
 
 Plots.jl

In [81]:
# so now we are ready to implement a hadamard design
pbw = 2 # Gauss
pbc = 4 # Gauss
N = 256 
nHad = 4 # number of hadamard sub-bands
indHad = 3 # let's design this specific hadamard function
tb = nHad * 4
θ = π / 2

# get a hadamard matrix
H = matrixdepot("hadamard", nHad)

# set up target pattern
@show T = (tb / nHad) / ((pbw / nHad) * γbar)
@show nCent = pbc * γbar * T # center of overall slab
ftw = dinf(sqrt(d1e / 2.0), d2e / sqrt(2.0)) / (tb / nHad) # 90-degree transition width relationship
f = [0, (1 - ftw) * (tb / (2 * nHad)), (1 + ftw) * (tb / (2 * nHad)), (N / 2)] / (N / 2) # passband edges for one subband
@show subbw = 2 * f[2] * (N / 2) # the width of each sub-band in integer units, including transition width
os = 8
x = (-N / 2 : 1 / os : N / 2 - 1 / os)
Mxd = ones(N * os, 1)
Myd = zeros(N * os, 1)
Mzd = zeros(N * os, 1)
w = ones(N * os, 1)

for ii = 0 : nHad - 1
    
    # add this subband's passband to Mzd/Mxd
    Mzd[abs.(collect(x .- nCent .- (ii - (nHad - 1) / 2) * subbw) ./ (N / 2)) .< f[2]] .= sin(θ) * H[indHad, ii + 1]
    Mzd[abs.(collect(x .+ nCent .+ (ii - (nHad - 1)/ 2) * subbw) ./ (N / 2)) .< f[2]] .= -sin(θ) * H[indHad, ii + 1]
    Mxd[abs.(collect(x .- nCent .- (ii - (nHad - 1)/ 2) * subbw) ./ (N / 2)) .< f[2]] .= cos(θ)
    Mxd[abs.(collect(x .+ nCent .+ (ii - (nHad - 1)/ 2) * subbw) ./ (N / 2)) .< f[2]] .= cos(θ)

    
    # add it to w as well
    w[abs.(collect(x .- nCent .- (ii - (nHad - 1) / 2) * subbw) ./ (N / 2)) .< f[3]] .= 0
    w[abs.(collect(x .- nCent .- (ii - (nHad - 1) / 2) * subbw) ./ (N / 2)) .< f[2]] .= d1e / d2e
    w[abs.(collect(x .+ nCent .+ (ii - (nHad - 1) / 2) * subbw) ./ (N / 2)) .< f[3]] .= 0
    w[abs.(collect(x .+ nCent .+ (ii - (nHad - 1) / 2) * subbw) ./ (N / 2)) .< f[2]] .= d1e / d2e


end

# plot em
plot(x, Mxd, label="Mx desired")
plot!(x, Myd, label="My desired")
plot!(x, Mzd, label="Mz desired")
plot!(x, w, label="weights")

T = (tb / nHad) / ((pbw / nHad) * γbar) = 0.0018788163457022077
nCent = pbc * γbar * T = 32.0
subbw = 2 * f[2] * (N / 2) = 2.5630379002540513


<!DOCTYPE html>
 
 
 Plots.jl

In [100]:
# TAKE 2- set up a tighter Hadamard design
pbw = 2 # Gauss - overall width of encoded slab
pbc = 2 # Gauss - center position of encoded slab
N = 256 
nHad = 4 # number of hadamard sub-bands
indHad = 2 # let's design this specific hadamard function
tb = nHad * 4
θ = π / 2

# get a hadamard matrix
H = matrixdepot("hadamard", nHad)

# set up target pattern
@show T = tb / (pbw * γbar)
@show nCent = pbc * γbar * T # center of overall slab
ftw = dinf(sqrt(d1e / 2.0), d2e / sqrt(2.0)) / tb # 90-degree transition width relationship
f = [0, (1 - ftw) * (tb / (2 * nHad)), (1 + ftw) * (tb / (2 * nHad)), (N / 2)] / (N / 2) # passband edges for one subband
@show subbw = 2 * f[3] * (N / 2) # the width of each sub-band in integer units, including transition width
os = 8
x = (-N / 2 : 1 / os : N / 2 - 1 / os)
Mxd = ones(N * os, 1)
Myd = zeros(N * os, 1)
Mzd = zeros(N * os, 1)
w = ones(N * os, 1)

for ii = 0 : nHad - 1
    
    # add this subband's passband to Mzd/Mxd
    Mzd[abs.(collect(x .- nCent .- (ii - (nHad - 1) / 2) * subbw)) .< (tb / (2 * nHad))] .= sin(θ) * H[indHad, ii + 1]
    Mzd[abs.(collect(x .+ nCent .+ (ii - (nHad - 1) / 2) * subbw)) .< (tb / (2 * nHad))] .= -sin(θ) * H[indHad, ii + 1]
    Mxd[abs.(collect(x .- nCent .- (ii - (nHad - 1) / 2) * subbw)) .< (tb / (2 * nHad))] .= cos(θ)
    Mxd[abs.(collect(x .+ nCent .+ (ii - (nHad - 1) / 2) * subbw)) .< (tb / (2 * nHad))] .= cos(θ)

    
    # add it to w as well
    w[abs.(collect(x .- nCent .- (ii - (nHad - 1) / 2) * subbw)) .<= (tb / (2 * nHad)) * 1.1] .= 0
    w[abs.(collect(x .- nCent .- (ii - (nHad - 1) / 2) * subbw)) .<= (tb / (2 * nHad)) * 0.9] .= d1e / d2e
    w[abs.(collect(x .+ nCent .+ (ii - (nHad - 1) / 2) * subbw)) .<= (tb / (2 * nHad)) * 1.1] .= 0
    w[abs.(collect(x .+ nCent .+ (ii - (nHad - 1) / 2) * subbw)) .<= (tb / (2 * nHad)) * 0.9] .= d1e / d2e


end

# plot em
plot(x, Mxd, label="Mx desired")
plot!(x, Myd, label="My desired")
plot!(x, Mzd, label="Mz desired")
plot!(x, w, label="weights")

T = tb / (pbw * γbar) = 0.0018788163457022077
nCent = pbc * γbar * T = 32.0
subbw = 2 * f[3] * (N / 2) = 4.359240524936487


<!DOCTYPE html>
 
 
 Plots.jl

In [101]:
# let's try to design it for zero phase, so that Mz = the magnitude of the above design, and others are zero
step = 0.0001
domoc = zeros(N, 1)
niters = 500
lamda = 10^-2
J = zeros(N, 1)
g = x -> ForwardDiff.gradient(myBlochSimErr, x)
@showprogress 1 "Computing..." for nn = 1 : niters
    J *= 0
    for ii = 1 : N * os
        rfg = [domoc; 2 * π * x[ii] / N; Mxd[ii]; Myd[ii]; Mzd[ii]; w[ii]]
        J += g(rfg)[1 : end - 5] .+ lamda * domoc
    end
    domoc -= step * J
end
plot(domoc ./ (2 * π * dt))
plot!(J)

Computing...100%|███████████████████████████████████████| Time: 0:08:24


<!DOCTYPE html>
 
 
 Plots.jl

In [102]:
# simulate it
Mxr = zeros(N * os, 1) # Mz
Myr = zeros(N * os, 1) # Mx
Mzr = zeros(N * os, 1) # My
for ii = 1 : N * os
    rfg = [domoc; 2 * π * x[ii] / N];
    M = BlochSimHalfB1Sel(rfg)
    Mxr[ii] = M[1]
    Myr[ii] = M[2]
    Mzr[ii] = M[3]
end
plot(x, abs.(Complex.(Myr, Mzr)), label="|Mxy|")
plot!(x, Myr, label="Mx")
plot!(x, Mzr, label="My")
plot!(x, Mzd, label="My, desired")
#plot!(x, abs.(Complex.(My, Mz)), label="|Mxy| desired")

<!DOCTYPE html>
 
 
 Plots.jl

In [103]:
# simulate it on a Gauss grid
b1 = -10 : 0.01 : 10
nb1 = length(b1)
Mxr = zeros(nb1, 1) # Mz
Myr = zeros(nb1, 1) # Mx
Mzr = zeros(nb1, 1) # My
for ii = 1 : nb1
    rfg = [domoc; b1[ii] * γ * T / N]
    M = BlochSimHalfB1Sel(rfg)
    Mxr[ii] = M[1]
    Myr[ii] = M[2]
    Mzr[ii] = M[3]
end
plot(b1, abs.(Complex.(Myr, Mzr)), label="|Mxy|")
plot!(b1, Myr, label="Mx")
plot!(b1, Mzr, label="My")
#plot!(x, abs.(Complex.(My, Mz)), label="|Mxy| desired")

<!DOCTYPE html>
 
 
 Plots.jl